# NDVI (Vegetationsindex)

## Räumliche und zeitliche Ausdehnung

Unterschungsbereich und Zeitraum festlegen.

In [ ]:
spatial_extent = {'west': 8.721771, 'south': 53.025027, 'east': 8.904419, 'north': 53.114965}

In [ ]:
temporal_extent = ["2020-01-01", "2021-01-01"]

## Authentifizierung

Um Satellitenbilder herunterzuladen wird ein Account bei [Dataspace Copernicus](https://dataspace.copernicus.eu) benötigt

In [ ]:
import openeo

connection = openeo.connect("https://openeo.dataspace.copernicus.eu/").authenticate_oidc()

In [ ]:
cube = connection.load_collection(
    "SENTINEL2_L2A", # Sentinel 2 Satellit
    spatial_extent=spatial_extent,
    temporal_extent=temporal_extent,
    bands=["B04", "B08"], # Rot- und Infrarotkanal
    max_cloud_cover=50
)

# Durchschnitt über alle Aufnahmezeitpunkte
cube = cube.mean_time()

# Werte skalieren
cube = cube.apply(lambda v: v * 0.0001)

# Rotes und Nah-Infrarot Band auslesen
red = cube.band("B04")
nir = cube.band("B08")

# NDVI berechnen
ndvi = (nir - red) / (nir + red)

# Data cube herunterladen
ndvi = ndvi.save_result(format="GTIFF")
job = ndvi.create_job(title="NDVI Image")
job.start_and_wait().download_result('results/ndvi.tif')

## Anzeige

In [ ]:
import leafmap

m = leafmap.Map()

m.add_raster('results/ndvi.tif', colormap='RdYlGn', vmin=-0.2, vmax=0.8)

m

## Daten einlesen

Mit `rasterio` können wir die Messwerte in einem Array einlesen, um damit weitere Analyse vorzunehmen.

In [ ]:
import rasterio as rio

# Datei öffnen
src = rio.open('results/ndvi.tif')

# Pixelwerte auslesen
data = src.read()

data

In [ ]:
import plotly.express as px

fig = px.imshow(
    data[0],
    color_continuous_scale='RdYlGn',
    color_continuous_midpoint=0.1,
    height=800
)

fig.show()